In [1]:
import pandas as pd
import numpy as np
import os

from shutil import copyfile
import json

import re
from tqdm import tqdm
pd.set_option('display.max_rows', 1000+1)

In [2]:
pdb_labeled_dir = 'dataset/Godess_gnn/preprocess_data/Godess_carbon_labeled_pdb_all/'
pdb_file_list = os.listdir(pdb_labeled_dir)

##### Delete illegal glycan from step 3

In [3]:
illegal_no_list = [17, 516, 214]
illegal_name_list = ['labeled_all_' + str(i) + '.pdb.csv' for i in illegal_no_list]

##### Reformulate shift values, relabel shift values for ranges, relabel empty/missing shifts

In [4]:
def reformulate_shift(pdb_f, pdb_f_name):

    shift_list = pdb_f['shift'].values
    
#     assert(isinstance(shift_list[0], str))
    
    if isinstance(shift_list[0], str):
    
        for i in range(len(shift_list)):
            
            if ( pd.isna(shift_list[i]) ) or (shift_list[i] == '?'):

                current_shift = '-1'

                pdb_f.loc[i, ['shift']] = current_shift
            
            elif pdb_f.loc[i, :]['Residual_accurate_name'] == 'Cho':
            
                pdb_f.loc[i, ['shift']] = '-1'
            

            elif ('-' in shift_list[i]) and (shift_list[i] != '-1') and (shift_list[i] != '-1.0') and \
                (len(shift_list[i]) > 2):
                
                current_shift = shift_list[i]

                reformulate_current_shift = current_shift.split('-')

                current_atom = pdb_f.loc[i, :]['Atom_name']

                current_atom_second = current_atom + '1'

                next_atom = pdb_f.loc[i+1, :]['Atom_name']

                if current_atom_second != next_atom:
#                     print(pdb_f_name, i, current_atom, 'next atom is not', current_atom_second, 
#                           'it is:', next_atom)

                    if current_atom == next_atom:

                        pdb_f.loc[i+1, ['Atom_name']] = current_atom_second

                    else:
                        raise Exception('Next atom is not consistent with current atom')
                        
#                 print(i, reformulate_current_shift, current_atom, current_atom_second)

                pdb_f.loc[i, ['shift']] = reformulate_current_shift[0]
                pdb_f.loc[i+1, ['shift']] = reformulate_current_shift[1]


            elif ('-' in shift_list[i]) and (len(shift_list[i]) == 1):
                print(pdb_f_name, i)
                
                current_shift = '-1'

                pdb_f.loc[i, ['shift']] = current_shift

        pdb_f_out = pdb_f.astype({'shift': 'float'})

        return pdb_f_out
    
    else:
        
        return pdb_f

##### Reformulate monosaccharides

In [5]:
glycan_list = ['gal', 'galnac', 'galn', 'gala', 'galanac', 'glc', 'glcnac', 'glcn', 'glca', 'fuc', 
               'man', 'mannac', 'mann', 'mana', 'kdn', 'neu5ac', 'xyl', 'idoa', 'neu5gc', 'kdo', 
               'kdn', 'qui',  'quinac', 'rhap', 'ara', 'gula', 'rib', 'neu5ac', 'tal', 'rha', 
               'rhanac', 'fucnac', 'rhanac', 'ido', '3,6anhgal', 'neu', 'fru', 'api', 'qui4n', 'galna', 'glcna',
              'fucn', 'qui3n', 'quin', 'rha4n', 'rhan']

non_mono_component_list = ['Ac', 'Asn', 'Gc', 'Me', 'P', 'S', 'Ser', 'Missing Monosaccharide', 'Cho', 'bu', 'bz',
                          'caf', 'fer', 'lyx', 'mal', 'myoIno', '17hoole', 'allyl', 'pcoum', 'gallic']
non_mono_component_list = [x.lower() for x in non_mono_component_list]
glycan_list_extend = glycan_list + non_mono_component_list

In [6]:
def split_single_mono_bound(mono):
    
    mono = mono.lower()
    
    ab = 'missing_a_b'
    ld = 'missing_L_D'
    abbrev = ''
    
    _ct = mono.count('-')
    temp_mono_list = mono.split('-')
    if _ct == 2:
        
        if mono in ['d-gal-ol', 'd-glc-ol', 'd-glcn-ol', 'l-ara-ol', 'd-rib-ol']:
            
            ld = mono.split('-')[0]
            abbrev = mono[2:]
            
        else:
        
            ab = temp_mono_list[0]
            ld = temp_mono_list[1]
            abbrev = temp_mono_list[2]
        
    elif _ct == 1:
#         the following are wired only one appeared
#         D-Glca
#         b-Neup
        temp_bound_incomp = temp_mono_list[0]
        
        if mono == 'kdo-ol' :
            
            temp_mono_list = ['', 'kdo-ol']
        
        elif temp_bound_incomp in ['delta', 'd', 'l']:
            ld = temp_bound_incomp
            
            if ld == 'delta':
                ld = 'd'
            
        elif temp_bound_incomp in ['a', 'b']:
            ab = temp_bound_incomp 
        
        abbrev = temp_mono_list[1]
    
    elif _ct == 0:
        abbrev = mono
        
    return ab, ld, abbrev

In [7]:
split_single_mono_bound('Kdo-ol')

('missing_a_b', 'missing_L_D', 'kdo-ol')

In [8]:
def reformulate_monosaccharide(abbrev, g_list):
    
    if abbrev == 'p':
        carbon_number = 'missing_carbon_number'
        current_split_list = [abbrev]
    
    elif abbrev in ['caf', 'pr', 'fer', 'pcoum']:
        carbon_number = 'missing_carbon_number'
        current_split_list = [abbrev]
    
    elif abbrev == 'apif':
        carbon_number = 'F'
        current_split_list = abbrev.split('f')
    
    elif abbrev == 'fucpn':
        carbon_number = 'P'
        current_split_list = ['fucn']
    
    elif 'p' in abbrev:
        carbon_number = 'P'
        current_split_list = abbrev.split('p')
    
    elif 'f' in abbrev:
        carbon_number = 'F'
        current_split_list = abbrev.split('f')
    
    else:
        carbon_number = 'missing_carbon_number'
        current_split_list = [abbrev]

    print(current_split_list)
    
    if current_split_list[0] in ['gal-ol', 'glc-ol', 'glcn-ol', 'rib-ol', 'kdo-ol', 'ara-ol', 'pr', 'fucn']:
        
        return abbrev, current_split_list[0], carbon_number
    
    new_abbrev = ''.join(current_split_list)
    

    indicator = 0

    for m in g_list:
        if (m in new_abbrev) and (indicator == 0):
            
            new_mono = m
            indicator = 1
            prev_m = m
        elif (m in new_abbrev) and (indicator == 1):
            
            if len(m) > len(prev_m):
                new_mono = m
            else:
                new_mono = prev_m

    if 'fru' in abbrev:
        new_mono = 'fru'
    
    elif indicator == 0:
        new_mono = 'missing monosaccharide'
    
    return abbrev, new_mono, carbon_number

In [9]:
reformulate_monosaccharide('fucpn', glycan_list_extend)

['fucn']


('fucpn', 'fucn', 'P')

In [10]:
def reformulate_pdb_monosaccharide(pdb_f):
    
    ab_list = []
    ld_list = []
    abbrev_list = []
    pf_list = []
    standard_abbrev_list = []
    
    residual_name_list = pdb_f['Residual_accurate_name'].values
    
    for mono in residual_name_list:
        
        ab, ld, abbrev = split_single_mono_bound(mono)
    
        abbrev, new_mono, carbon_number = reformulate_monosaccharide(abbrev, glycan_list_extend)


        ab_list.append(ab)
        ld_list.append(ld)
        abbrev_list.append(abbrev)
        standard_abbrev_list.append(new_mono)
        pf_list.append(carbon_number)

        del ab, ld, abbrev, new_mono, carbon_number
        
    pdb_f_copy = pdb_f.copy()
    
    assert(len(ab_list) == len(pdb_f))
    assert(len(ld_list) == len(pdb_f))
    assert(len(standard_abbrev_list) == len(pdb_f))
    assert(len(abbrev_list) == len(pdb_f))
    assert(len(pf_list) == len(pdb_f))
    
    pdb_f_copy['bound_AB'] = ab_list
    pdb_f_copy['fischer_projection_DL'] = ld_list
    pdb_f_copy['origin_mono'] = abbrev_list
    pdb_f_copy['reformulated_standard_mono'] = standard_abbrev_list
    pdb_f_copy['carbon_number_PF'] = pf_list
    
    return pdb_f_copy

##### Combine the above three steps

In [11]:
out_dir = 'dataset/Godess_final_data/Godess_data/'

In [12]:
# pdb_f = pd.read_csv('dataset/Godess_gnn/preprocess_data/Godess_carbon_labeled_pdb_all/labeled_all_' 
#                             +str(17) + '.pdb.csv')
# 'Godess_carbon_labeled_pdb_all/labeled_all_' +str(17) + '.pdb.csv'

In [13]:
# mono_list = ['Ac', 'Asn', 'D-Glca', 'Gc', 'Me', 'Missing Monosaccharide', 'P',
#        'S', 'Ser', 'a-D-3,6anhGalp', 'a-D-Fruf', 'a-D-Frup', 'a-D-Fucp',
#        'a-D-Galf', 'a-D-Galp', 'a-D-GalpA', 'a-D-GalpN', 'a-D-Glcp',
#        'a-D-GlcpA', 'a-D-GlcpN', 'a-D-Manp', 'a-D-ManpA', 'a-D-Xylp',
#        'a-L-3,6anhGalp', 'a-L-Araf', 'a-L-Fucp', 'a-L-Galp', 'a-L-GulpA',
#        'a-L-IdopA', 'a-L-Rhap', 'a-Neup', 'b-D-Fruf', 'b-D-Frup',
#        'b-D-Fucp', 'b-D-Galp', 'b-D-GalpA', 'b-D-GalpN', 'b-D-Glcp',
#        'b-D-GlcpA', 'b-D-GlcpN', 'b-D-Manp', 'b-D-ManpA', 'b-D-Xylp',
#        'b-L-3,6anhGalp', 'b-L-Fucp', 'b-Neup']

In [14]:
mono_list = []

In [15]:
for i in tqdm(range(len(pdb_file_list))):

# for i in [928]:
# for i in [262]:
# for i in [1809]:
# for i in [101]:
    pdb_f_name = pdb_file_list[i]
    
    # ignore illegal name
    if pdb_f_name in illegal_name_list:
        continue
    

    
    pdb_f_path = os.path.join(pdb_labeled_dir, pdb_f_name)
    pdb_f = pd.read_csv(pdb_f_path)
    
    # reformulate shift value
    pdb_f = reformulate_shift(pdb_f, pdb_f_name)
    
    
    # reformulate monosaccharide name
    pdb_f = reformulate_pdb_monosaccharide(pdb_f)
    pdb_f['Atom_type'] = pdb_f[['Atom_type']].replace({'0': 'O'})
    
    out_path_f = os.path.join(out_dir, pdb_f_name)
    
    pdb_f.to_csv(out_path_f, index = False)

    mono_list.extend(list(np.unique(pdb_f['Residual_accurate_name'].values)))

  0%|                                          | 6/2402 [00:00<00:41, 57.83it/s]

['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['rha', '']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', 

['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['s']
['s']
['s'

  0%|▏                                        | 12/2402 [00:00<00:57, 41.45it/s]

['me']
['me']
['me']
['me']
['me']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'a']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['g

...

labeled_all_1441.pdb.csv 68
labeled_all_1441.pdb.csv 155
labeled_all_1441.pdb.csv 181
['me']
['me']
['me']
['me']
['me']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['fuc', '']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['s']
['s']
['s']
['s']
['s']
['gal', '']
['gal', '']
['gal',

100%|██████████████████████████████████████▉| 2400/2402 [00:56<00:00, 45.90it/s]

labeled_all_492.pdb.csv 68
labeled_all_492.pdb.csv 127
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', 'n']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal', '']
['gal'

100%|███████████████████████████████████████| 2402/2402 [00:56<00:00, 42.64it/s]

['me']
['me']
['me']
['me']
['me']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['man', 'a']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['glc', '']
['s']
['s']
['s']
['s']
['s']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc', 'n']
['glc'

In [16]:
len(pdb_file_list)

2402

In [17]:
out_path_f

'dataset/Godess_final_data/Godess_data/labeled_all_1494.pdb.csv'

In [18]:
pdb_f_name

'labeled_all_1494.pdb.csv'

In [19]:
df_match = pd.read_csv('new_matching_table.csv')
df_match.loc[df_match['2'] == 2358]

0   1     2
2357  Glycoscience_Linear_Nonlinear/  74  2358

In [20]:
pdb_f = pdb_f[['Atom_type']].replace({'0': 'O'})

In [21]:
mono_list = ['17HOOle', 'Ac', 'Allyl', 'Asn', 'Bu', 'Bz', 'Caf', 'Cho',
       'D-Gal-ol', 'D-Glc-ol', 'D-GlcN-ol', 'D-Glca', 'D-Rib-ol', 'Fer',
       'Gallic', 'Gc', 'Kdo-ol', 'L-Ara-ol', 'Mal', 'Me',
       'Missing Monosaccharide', 'P', 'Pr', 'S', 'Ser', 'a-D-3,6anhGalp',
       'a-D-Apif', 'a-D-Araf', 'a-D-Fruf', 'a-D-Frup', 'a-D-Fucp',
       'a-D-FucpN', 'a-D-Galf', 'a-D-Galp', 'a-D-GalpA', 'a-D-GalpN',
       'a-D-GalpNA', 'a-D-Glcp', 'a-D-GlcpA', 'a-D-GlcpN', 'a-D-GlcpNA',
       'a-D-Idop', 'a-D-Lyxp', 'a-D-Manp', 'a-D-ManpA', 'a-D-ManpN',
       'a-D-Quip4N', 'a-D-Rhap', 'a-D-Rhap4N', 'a-D-RhapN', 'a-D-Ribf',
       'a-D-Ribp', 'a-D-Xylp', 'a-Kdop', 'a-L-3,6anhGalp', 'a-L-6dTalp',
       'a-L-Araf', 'a-L-Arap', 'a-L-Fucp', 'a-L-FucpN', 'a-L-Galp',
       'a-L-GulpA', 'a-L-IdopA', 'a-L-Rhap', 'a-Neup', 'b-D-Apif',
       'b-D-Araf', 'b-D-Fruf', 'b-D-Frup', 'b-D-Fucp', 'b-D-FucpN',
       'b-D-Galf', 'b-D-Galp', 'b-D-GalpA', 'b-D-GalpN', 'b-D-GalpNA',
       'b-D-Glcp', 'b-D-GlcpA', 'b-D-GlcpN', 'b-D-GlcpNA', 'b-D-Idop',
       'b-D-Lyxp', 'b-D-Manp', 'b-D-ManpA', 'b-D-ManpN', 'b-D-Quip',
       'b-D-Quip3N', 'b-D-Quip4N', 'b-D-QuipN', 'b-D-Rhap', 'b-D-Rhap4N',
       'b-D-Ribf', 'b-D-Ribp', 'b-D-Xylp', 'b-Galf', 'b-Kdop',
       'b-L-3,6anhGalp', 'b-L-Arap', 'b-L-Fucp', 'b-L-Galp', 'b-L-Rhap',
       'b-L-RhapN', 'b-L-Xylp', 'b-Neup', 'myoIno', 'pCoum']

In [22]:
mono_list = np.unique(mono_list)

In [23]:
ab_list = []
ld_list = []
abbrev_list = []
pf_list = []
standard_abbrev_list = []

In [24]:
for mono in np.unique(np.unique(mono_list)):

# for mono in ['missing monosaccharide']:

    ab, ld, abbrev = split_single_mono_bound(mono)
    
    abbrev, new_mono, carbon_number = reformulate_monosaccharide(abbrev, glycan_list_extend)
    
    
    ab_list.append(ab)
    ld_list.append(ld)
    abbrev_list.append(abbrev)
    standard_abbrev_list.append(new_mono)
    pf_list.append(carbon_number)
    
    del ab, ld, abbrev, new_mono, carbon_number
    

['17hoole']
['ac']
['allyl']
['asn']
['bu']
['bz']
['caf']
['cho']
['gal-ol']
['glc-ol']
['glcn-ol']
['glca']
['rib-ol']
['fer']
['gallic']
['gc']
['kdo-ol']
['ara-ol']
['mal']
['me']
['missing monosaccharide']
['p']
['pr']
['s']
['ser']
['3,6anhgal', '']
['api', '']
['ara', '']
['', 'ru', '']
['fru', '']
['fuc', '']
['fucn']
['gal', '']
['gal', '']
['gal', 'a']
['gal', 'n']
['gal', 'na']
['glc', '']
['glc', 'a']
['glc', 'n']
['glc', 'na']
['ido', '']
['lyx', '']
['man', '']
['man', 'a']
['man', 'n']
['qui', '4n']
['rha', '']
['rha', '4n']
['rha', 'n']
['rib', '']
['rib', '']
['xyl', '']
['kdo', '']
['3,6anhgal', '']
['6dtal', '']
['ara', '']
['ara', '']
['fuc', '']
['fucn']
['gal', '']
['gul', 'a']
['ido', 'a']
['rha', '']
['neu', '']
['api', '']
['ara', '']
['', 'ru', '']
['fru', '']
['fuc', '']
['fucn']
['gal', '']
['gal', '']
['gal', 'a']
['gal', 'n']
['gal', 'na']
['glc', '']
['glc', 'a']
['glc', 'n']
['glc', 'na']
['ido', '']
['lyx', '']
['man', '']
['man', 'a']
['man', 'n']
['qu

In [25]:
mono_list[[8, 9, 10, 17]]

array(['D-Gal-ol', 'D-Glc-ol', 'D-GlcN-ol', 'L-Ara-ol'], dtype='<U22')

In [26]:
pd.DataFrame([mono_list, ab_list, ld_list, \
              abbrev_list, pf_list, standard_abbrev_list]).T

0            1            2                       3  \
0                   17HOOle  missing_a_b  missing_L_D                 17hoole   
1                        Ac  missing_a_b  missing_L_D                      ac   
2                     Allyl  missing_a_b  missing_L_D                   allyl   
3                       Asn  missing_a_b  missing_L_D                     asn   
4                        Bu  missing_a_b  missing_L_D                      bu   
5                        Bz  missing_a_b  missing_L_D                      bz   
6                       Caf  missing_a_b  missing_L_D                     caf   
7                       Cho  missing_a_b  missing_L_D                     cho   
8                  D-Gal-ol  missing_a_b            d                  gal-ol   
9                  D-Glc-ol  missing_a_b            d                  glc-ol   
10                D-GlcN-ol  missing_a_b            d                 glcn-ol   
11                   D-Glca  missing_a_b            d                    glca   
12                 D-Rib-ol  missing_a_b            d                  rib-ol   
13                      Fer  missing_a_b  missing_L_D                     fer   
14                   Gallic  missing_a_b  missing_L_D                  gallic   
15                       Gc  missing_a_b  missing_L_D                      gc   
16                   Kdo-ol  missing_a_b  missing_L_D                  kdo-ol   
17                 L-Ara-ol  missing_a_b            l                  ara-ol   
18                      Mal  missing_a_b  missing_L_D                     mal   
19                       Me  missing_a_b  missing_L_D                      me   
20   Missing Monosaccharide  missing_a_b  missing_L_D  missing monosaccharide   
21                        P  missing_a_b  missing_L_D                       p   
22                       Pr  missing_a_b  missing_L_D                      pr   
23                        S  missing_a_b  missing_L_D                       s   
24                      Ser  missing_a_b  missing_L_D                     ser   
25           a-D-3,6anhGalp            a            d              3,6anhgalp   
26                 a-D-Apif            a            d                    apif   
27                 a-D-Araf            a            d                    araf   
28                 a-D-Fruf            a            d                    fruf   
29                 a-D-Frup            a            d                    frup   
30                 a-D-Fucp            a            d                    fucp   
31                a-D-FucpN            a            d                   fucpn   
32                 a-D-Galf            a            d                    galf   
33                 a-D-Galp            a            d                    galp   
34                a-D-GalpA            a            d                   galpa   
35                a-D-GalpN            a            d                   galpn   
36               a-D-GalpNA            a            d                  galpna   
37                 a-D-Glcp            a            d                    glcp   
38                a-D-GlcpA            a            d                   glcpa   
39                a-D-GlcpN            a            d                   glcpn   
40               a-D-GlcpNA            a            d                  glcpna   
41                 a-D-Idop            a            d                    idop   
42                 a-D-Lyxp            a            d                    lyxp   
43                 a-D-Manp            a            d                    manp   
44                a-D-ManpA            a            d                   manpa   
45                a-D-ManpN            a            d                   manpn   
46               a-D-Quip4N            a            d                  quip4n   
47                 a-D-Rhap            a            d                    rhap   
48               a-D-Rhap4N            a            d    

In [27]:
pd.DataFrame([mono_list, ab_list, ld_list, \
              abbrev_list, pf_list, standard_abbrev_list]).T.to_csv('new_encode_mono.csv', index = False)

In [28]:
# # def reformulate_shift(pdb_f, pdb_f_name):

# shift_list = pdb_f['shift'].values

# if isinstance(shift_list[0], str):


#     for i in range(len(shift_list)):

#         if ( pd.isna(shift_list[i]) ) or (shift_list[i] == '?'):

#             current_shift = '-1'

#             pdb_f.loc[i, ['shift']] = current_shift

#         elif ('-' in shift_list[i]) and (shift_list[i] != '-1') and (shift_list[i] != '-1.0') and (len(shift_list[i]) > 2):

#             current_shift = shift_list[i]

#             reformulate_current_shift = current_shift.split('-')

#             current_atom = pdb_f.loc[i, :]['Atom_name']

#             current_atom_second = current_atom + '1'

#             next_atom = pdb_f.loc[i+1, :]['Atom_name']

#             if current_atom_second != next_atom:
#                 print(pdb_f_name, i, current_atom, 'next atom is not', current_atom_second)

#                 if current_atom == next_atom:

#                     pdb_f.loc[i+1, :]['Atom_name'] = current_atom_second
#                     print(current_atom_second)
                    
#                 else:

#                     raise Exception(i, 'Next atom is not consistent with current atom')

#             print(i, reformulate_current_shift, current_atom, current_atom_second)

#             pdb_f.loc[i, ['shift']] = reformulate_current_shift[0]
#             pdb_f.loc[i+1, ['shift']] = reformulate_current_shift[1]


#         elif ('-' in shift_list[i]) and (len(shift_list[i]) == 1):
            
#             current_shift = '-1'

#             pdb_f.loc[i, ['shift']] = current_shift

#     pdb_f_out = pdb_f.astype({'shift': 'float'})


In [29]:
# pdb_f

In [30]:
# shift_list[0]